### Installing Libraries

In [4]:
!pip install geopandas

### Importing Libraries

In [5]:
import numpy as np
import pandas as pd
import geopandas as gpd
!pip install folium
import folium
from folium import plugins
import datetime

from IPython.display import HTML, display

from folium.plugins import TimestampedGeoJson

### Importing the data as Pandas DataFrame

In [6]:
fp = "https://earthquake.usgs.gov/earthquakes/feed/v1.0/summary/all_month.csv"
eartt=pd.read_csv(fp)
eartt.head()

time   latitude   longitude   depth   mag magType  \
0  2023-11-16T15:34:08.460Z  33.988834 -117.119003   8.200  1.17      ml   
1  2023-11-16T15:33:17.247Z  61.294000 -152.250300   7.500  1.10      ml   
2  2023-11-16T15:28:09.858Z  63.899900 -150.410900   0.000  1.90      ml   
3  2023-11-16T15:00:27.431Z  62.849300 -150.564300  80.000  1.60      ml   
4  2023-11-16T14:59:29.813Z   9.413600  126.235100  70.306  4.60      mb   

    nst    gap    dmin   rms  ...                   updated  \
0  16.0  136.0  0.1845  0.29  ...  2023-11-16T15:40:32.048Z   
1   NaN    NaN     NaN  0.11  ...  2023-11-16T15:35:26.783Z   
2   NaN    NaN     NaN  0.57  ...  2023-11-16T15:30:26.668Z   
3   NaN    NaN     NaN  0.33  ...  2023-11-16T15:02:08.353Z   
4  29.0  128.0  2.4180  0.68  ...  2023-11-16T15:34:06.040Z   

                              place        type horizontalError depthError  \
0            6 km W of Calimesa, CA  earthquake            0.88      5.420   
1                   Southern Alaska  earthquake             NaN      0.400   
2        64 km WSW of Ferry, Alaska  earthquake             NaN      0.500   
3                    Central Alaska  earthquake             NaN      0.800   
4  15 km NNE of Cortes, Philippines  earthquake           10.77      5.905   

   magError  magNst     status  locationSource magSource  
0     0.283    12.0  automatic              ci        ci  
1       NaN     NaN  automatic              ak        ak  
2       NaN     NaN  automatic              ak        ak  
3       NaN     NaN  automatic              ak        ak  
4     0.092    35.0   reviewed              us        us  

[5 rows x 22 columns]

### Rename the name of the column

In [8]:
eartt1=eartt.rename({'time':'time_hour'}, axis=1)
eartt1.head()

time_hour   latitude   longitude   depth   mag magType  \
0  2023-11-16T15:34:08.460Z  33.988834 -117.119003   8.200  1.17      ml   
1  2023-11-16T15:33:17.247Z  61.294000 -152.250300   7.500  1.10      ml   
2  2023-11-16T15:28:09.858Z  63.899900 -150.410900   0.000  1.90      ml   
3  2023-11-16T15:00:27.431Z  62.849300 -150.564300  80.000  1.60      ml   
4  2023-11-16T14:59:29.813Z   9.413600  126.235100  70.306  4.60      mb   

    nst    gap    dmin   rms  ...                   updated  \
0  16.0  136.0  0.1845  0.29  ...  2023-11-16T15:40:32.048Z   
1   NaN    NaN     NaN  0.11  ...  2023-11-16T15:35:26.783Z   
2   NaN    NaN     NaN  0.57  ...  2023-11-16T15:30:26.668Z   
3   NaN    NaN     NaN  0.33  ...  2023-11-16T15:02:08.353Z   
4  29.0  128.0  2.4180  0.68  ...  2023-11-16T15:34:06.040Z   

                              place        type horizontalError depthError  \
0            6 km W of Calimesa, CA  earthquake            0.88      5.420   
1                   Southern Alaska  earthquake             NaN      0.400   
2        64 km WSW of Ferry, Alaska  earthquake             NaN      0.500   
3                    Central Alaska  earthquake             NaN      0.800   
4  15 km NNE of Cortes, Philippines  earthquake           10.77      5.905   

   magError  magNst     status  locationSource magSource  
0     0.283    12.0  automatic              ci        ci  
1       NaN     NaN  automatic              ak        ak  
2       NaN     NaN  automatic              ak        ak  
3       NaN     NaN  automatic              ak        ak  
4     0.092    35.0   reviewed              us        us  

[5 rows x 22 columns]

### The time is imported  as text (strings)

In [9]:
type(eartt1.loc[0,'time_hour'])

str

### Changing time to datetime



In [10]:
eartt1['time_hour']=eartt1['time_hour'].str[:-5]
eartt1['time_hour']=pd.to_datetime(eartt1['time_hour'])

###Time as the data frame's index
###Create a new column called "type" to help us in the pivoting

In [11]:
eartt1=eartt1.set_index('time_hour')
eartt1['type']= 'ss'
eartt1.head(1)


latitude   longitude  depth   mag magType   nst    gap  \
time_hour                                                                      
2023-11-16 15:34:08  33.988834 -117.119003    8.2  1.17      ml  16.0  136.0   

                       dmin   rms net  ...                   updated  \
time_hour                              ...                             
2023-11-16 15:34:08  0.1845  0.29  ci  ...  2023-11-16T15:40:32.048Z   

                                      place type horizontalError  depthError  \
time_hour                                                                      
2023-11-16 15:34:08  6 km W of Calimesa, CA   ss            0.88        5.42   

                     magError  magNst     status locationSource magSource  
time_hour                                                                  
2023-11-16 15:34:08     0.283    12.0  automatic             ci        ci  

[1 rows x 21 columns]

### List number of earquakes by place, time, location, magnitude

In [12]:
start = eartt1.pivot_table('id',
                          index = ['place', 'time_hour',
                                   'latitude',
                                   'longitude', 
                                   'mag'
                                   ],
                          columns = 'type',
                          aggfunc='count').reset_index()




start.head()

type                             place           time_hour   latitude  \
0            0 km E of Hospital, Chile 2023-11-05 15:48:11 -20.214300   
1      0 km E of Howardville, Missouri 2023-11-09 12:37:18  36.568333   
2        0 km E of Indios, Puerto Rico 2023-11-07 10:02:52  17.994667   
3           0 km ENE of Pāhala, Hawaii 2023-11-14 01:31:31  19.203167   
4     0 km ESE of Oakville, Washington 2023-10-25 22:50:14  46.839833   

type   longitude   mag  ss  
0     -70.132300  3.30   1  
1     -89.597000  1.61   1  
2     -66.811333  2.64   1  
3    -155.477829  1.84   1  
4    -123.229333  1.55   1

### Extract the hour from time_hour

In [13]:
start['time_hour']=pd.to_datetime(start['time_hour'])
start['time_hh']=start['time_hour'].dt.hour
start.head()


type                             place           time_hour   latitude  \
0            0 km E of Hospital, Chile 2023-11-05 15:48:11 -20.214300   
1      0 km E of Howardville, Missouri 2023-11-09 12:37:18  36.568333   
2        0 km E of Indios, Puerto Rico 2023-11-07 10:02:52  17.994667   
3           0 km ENE of Pāhala, Hawaii 2023-11-14 01:31:31  19.203167   
4     0 km ESE of Oakville, Washington 2023-10-25 22:50:14  46.839833   

type   longitude   mag  ss  time_hh  
0     -70.132300  3.30   1       15  
1     -89.597000  1.61   1       12  
2     -66.811333  2.64   1       10  
3    -155.477829  1.84   1        1  
4    -123.229333  1.55   1       22

### Choosing color depending on the magnitude for each Earthquake
3352FF Blue

FCFF33 Yellow

FF33EC Pink 

FF334C Red

In [14]:
start.loc[start['mag']<7, 'fillcolor']='#3352FF ' # Earthquakes with magnitude less than 7  = blue color
start.loc[start['mag']>=7, 'fillcolor']='#FF33EC' # Earthquakes with magnitude bigger or equal than 7  = pink color
start.loc[start['mag']>=8, 'fillcolor']='#FCFF33' # Earthquakes with magnitude bigger or equal than 8  = yellow color
start.loc[start['mag']>=9, 'fillcolor']='#FF334C' # Earthquakes with magnitude bigger or equal than 9  = red color


In [15]:
start.shape

(9832, 8)

In [16]:
start.head()

type                             place           time_hour   latitude  \
0            0 km E of Hospital, Chile 2023-11-05 15:48:11 -20.214300   
1      0 km E of Howardville, Missouri 2023-11-09 12:37:18  36.568333   
2        0 km E of Indios, Puerto Rico 2023-11-07 10:02:52  17.994667   
3           0 km ENE of Pāhala, Hawaii 2023-11-14 01:31:31  19.203167   
4     0 km ESE of Oakville, Washington 2023-10-25 22:50:14  46.839833   

type   longitude   mag  ss  time_hh fillcolor  
0     -70.132300  3.30   1       15  #3352FF   
1     -89.597000  1.61   1       12  #3352FF   
2     -66.811333  2.64   1       10  #3352FF   
3    -155.477829  1.84   1        1  #3352FF   
4    -123.229333  1.55   1       22  #3352FF

### Normalizing magnitude with max and min values

In [17]:
start['mag']= (start['mag'] - start['mag'].min())/(start['mag'].max()-start['mag'].min())
#df["A"] = (df["A"]-df["A"].min()) / (df["A"].max()-df["A"].min())
start['mag'].head()

0    0.548694
1    0.347981
2    0.470309
3    0.375297
4    0.340855
Name: mag, dtype: float64

### Function to create the features of the animation: time, location, icon to represent magnitude of Earthquake, etc

In [18]:
def create_geojson_features(df):
    features = []
    
    for _, row in df.iterrows():
        feature = {
            'type': 'Feature',
            'geometry': {
                'type':'Point', 
                'coordinates':[row['longitude'],row['latitude']]
            },
            'properties': {
                'time': pd.to_datetime(row['time_hour'], unit='h').__str__(),
                'style': {'color' : ''},
                'icon': 'circle',
                'iconstyle':{
                    'fillColor': row['fillcolor'],
                    'fillOpacity': 0.8,
                    'stroke': 'true',
                    'radius': row['mag']*10
                }
            }
        }
        features.append(feature)
    return features


### Calling the Function create_geojson_features and using it in our data frame and get the geojson

In [19]:
start_geojson = create_geojson_features(start)
start_geojson[0]

{'type': 'Feature',
 'geometry': {'type': 'Point', 'coordinates': [-70.1323, -20.2143]},
 'properties': {'time': '2023-11-05 15:48:11',
  'style': {'color': ''},
  'icon': 'circle',
  'iconstyle': {'fillColor': '#3352FF ',
   'fillOpacity': 0.8,
   'stroke': 'true',
   'radius': 5.486935866983373}}}

### Creating Interactive And Animated Map

In [21]:


EQ_map = folium.Map(location = [2, -2],
                    tiles = "CartoDB Positron",
                    zoom_start = 2)
plugins.ScrollZoomToggler().add_to(EQ_map)

icon_plane = plugins.BeautifyIcon(
    icon="plane", border_color="#b3334f", text_color="#b3334f", icon_shape="triangle"
)

icon_number = plugins.BeautifyIcon(
    border_color="#00ABDC",
    text_color="#00ABDC",
    number=10,
    inner_icon_style="margin-top:0;",
)



folium.Marker(location=[50, -122], popup="Portland, OR", icon=icon_number).add_to(EQ_map)

plugins.Fullscreen(
    position="topright",
    title="Expand me",
    title_cancel="Exit me",
    force_separate_button=True,
).add_to(EQ_map)


TimestampedGeoJson(start_geojson,
                  period = 'PT1H',
                  duration = 'PT1H',
                  transition_time = 1000,
                  auto_play = True).add_to(EQ_map)

EQ_map

In [ ]:
EQ_map.save('EQ_map.html', title='Earthquakes with Magnitude 6 and higher since 1968')